In [22]:
#%%
import os, sys, re
path = []
for p in sys.path:
    if "RMG-Py" in p:
        continue
        #path.append('/work/westgroup/Importer/RMG-Py#/')
    else:
        path.append(p)
sys.path = path
import numpy as np

import pickle
import logging
import subprocess
import yaml
logger = logging.getLogger('my-logger')
logger.propagate = False
from autotst.reaction import Reaction, TS
from autotst.species import Species, Conformer
import multiprocessing
from multiprocessing import Manager, Process

import rmgpy
from rmgpy.thermo import NASA, ThermoData, Wilhoit, NASAPolynomial
import rmgpy.constants as constants
from rmgpy.kinetics import Arrhenius, ArrheniusEP, ThirdBody, Lindemann, Troe, \
                           PDepArrhenius, MultiArrhenius, MultiPDepArrhenius, \
                           Chebyshev, KineticsData, PDepKineticsModel
from rmgpy.data.kinetics.library import KineticsLibrary
from rmgpy.data.thermo import ThermoLibrary
from rmgpy.molecule import Molecule as RMGMolecule 
from rmgpy.species import Species as RMGSpecies
from rmgpy.reaction import Reaction as RMGReaction

from autotst.data.inputoutput import InputOutput, get_possible_names
import ck2cti


In [12]:
models_directories = {
    '../models/2028-Sarathy/':'../alternatives/butanol',
    '../models/n-Heptane/':'../alternatives/heptane',
    '../models/335-Wang/':'../alternatives/methylheptane'
}

parsers = {}

for dirpath, alternate_dirpath in models_directories.items():
    species_filepath = os.path.join(dirpath,  "RMG-Py-kinetics-library", "dictionary.txt")
    species_dict = rmgpy.data.kinetics.KineticsLibrary().get_species(species_filepath)
    species_list = [sp for sp in species_dict.values()]

    with open(os.path.join(dirpath,'import.sh')) as infile:
        shellscript = infile.read()

    reactions_filename = re.search('--reactions\s+(\S+)',shellscript).group(1)
    reactions_filepath = os.path.join(dirpath,reactions_filename)

    thermo_filename = re.search('--thermo\s+(\S+)',shellscript).group(1)
    thermo_filepath = os.path.join(dirpath,thermo_filename)

    parser = ck2cti.Parser()
    surfaces = parser.convertMech(inputFile=reactions_filepath,
                                    thermoFile=thermo_filepath,
                                    transportFile=None,
                                    surfaceFile=None,
                                    phaseName='gas',
                                    outName=os.path.join(alternate_dirpath,'master.cti'),
                                    permissive=True)
    
    parsers[alternate_dirpath.split('/')[-1]] = (parser, species_list)
    
parsers

ck2cti.py:953 warn WARNING Found reversible reaction containing a product photon:
oh*<=>oh+hv                                  1.450e+06      0.0           0.0
If the "--permissive" option was specified, this will be converted to an irreversible reaction with the photon removed.
ck2cti.py:953 warn WARNING Found reversible reaction containing a product photon:
ch*<=>ch+hv 1.860e+06 0.0 0.0
If the "--permissive" option was specified, this will be converted to an irreversible reaction with the photon removed.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "hoco" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ch3cho2h" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ch3coch2o2h" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ch3coch2o" while reading thermodynamics entry.
ck2cti.py:953 warn WARNING Found additional 

ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "o2c5h10oh-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c6h6" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c*ccjc*c" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c6h5" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c6h2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c6h3" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "l-c6h4" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c-c6h4" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c6h5oh" while reading thermodynamics entry.
ck2cti.py:1746 loadC

ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4o5h223" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4o5h212" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4o5h213" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4o5h2m1" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4o5h2m2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4o5h2m3" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4ohket1-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4ohket1-3" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "sc4ohket1-m" while reading thermody

Wrote CTI mechanism file to '../alternatives/butanol/master.cti'.
Mechanism contains 431 species and 2346 reactions.


ck2cti.py:953 warn WARNING Found additional declaration of species TIC4H7Q2-I
ck2cti.py:953 warn WARNING Found additional declaration of species IIC4H7Q2-T
ck2cti.py:953 warn WARNING Found additional declaration of species IIC4H7Q2-I
ck2cti.py:953 warn WARNING Found additional declaration of species CH2O2H
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "HOCO" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "CH3CHO2H" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "CH3CHCHO" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "C3H51-2V3OOH" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "C3H52-1V3OOH" while reading thermodynamics entry.
ck2cti.py:953 warn WARNING Found additional thermo entry for species C5H11O-1. If --permissive was given, the first entry is used.
ck

...

ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket6-3-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket6-4-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket6-5-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket6-7-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket6-8-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket6-9-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket6-10-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket7-3-2" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c20ket7-4-2" while rea

ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic14h29coc2h4p" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic3h7coc3h7" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic4h9coc3h7" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic5h11coc3h7" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic6h13coc3h7" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic7h15coc3h7" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic8h17coc3h7" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic9h19coc3h7" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "ic9h19coc3h6p" 

ck2cti.py:953 warn WARNING Found additional thermo entry for species c7h16-3. If --permissive was given, the first entry is used.
ck2cti.py:953 warn WARNING Found additional thermo entry for species c7h15-3a. If --permissive was given, the first entry is used.
ck2cti.py:953 warn WARNING Found additional thermo entry for species c7h15-3b. If --permissive was given, the first entry is used.
ck2cti.py:953 warn WARNING Found additional thermo entry for species c7h15-3c. If --permissive was given, the first entry is used.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c8h15-1a-3" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c8h15-2a-3" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c8h15-3a-3" while reading thermodynamics entry.
ck2cti.py:1746 loadChemkinFile INFO Skipping unexpected species "c8h15-4a-3" while reading thermodynamics entry.
ck2cti.py:1746 loadChemki

Wrote CTI mechanism file to '../alternatives/methylheptane/master.cti'.
Mechanism contains 1378 species and 8143 reactions.


{'butanol': (<ck2cti.Parser at 0x7faadd9b9750>,
  [Species(label="sc4h7oh-1ooh-3", molecule=[Molecule(smiles="[CH2]CC(C)(O)OO")], molecular_weight=(105.112,'amu')),
   Species(label="sc4h7oh-1ooh-2", molecule=[Molecule(smiles="C[CH]C(C)(O)OO")], molecular_weight=(105.112,'amu')),
   Species(label="c4h7oh-3ooh-1", molecule=[Molecule(smiles="CC(C[CH]O)OO")], molecular_weight=(105.112,'amu')),
   Species(label="tc4h8ooh-io2", molecule=[Molecule(smiles="CC(C)(CO[O])OO")], molecular_weight=(121.112,'amu')),
   Species(label="ic4h7oh-2ooh-1o2", molecule=[Molecule(smiles="CC(C)(OO)C(O)O[O]")], molecular_weight=(137.111,'amu')),
   Species(label="sc4ohket3-2", molecule=[Molecule(smiles="CC(O)(CC=O)OO")], molecular_weight=(120.104,'amu')),
   Species(label="c4h8oh-1o2h", molecule=[Molecule(smiles="CCCC(O)OO")], molecular_weight=(106.12,'amu')),
   Species(label="ch3o", molecule=[Molecule(smiles="C[O]")], molecular_weight=(31.0339,'amu')),
   Species(label="o2ch2och2o2h", molecule=[Molecule(smil

In [19]:
import shutil
# copying fake results just to make things run
for master_dir, sub_dirs, files in os.walk('../../autotst-2.0/autotst-1.0-results/'):
    for f in files:
        if f.endswith('.kinetics'):
            shutil.copyfile(
                os.path.join(master_dir, f),
                os.path.join('../_fake_results', f)
            )


In [28]:
reactions_to_process = {}

atst_dir = '../autotst-results/'
atst_dir = '../_fake_results/'
rmg_reactions = np.load('../find-reactions/autotst-reactions.npy')

for rmg_reaction in rmg_reactions:
    atst_reaction = Reaction(rmg_reaction = rmg_reaction)
    labeled_reaction, family = atst_reaction.get_labeled_reaction()
    
    possible_names = get_possible_names(
        [s.to_smiles() for s in labeled_reaction.reactants],
        [s.to_smiles() for s in labeled_reaction.products]
    )
    found_result = False
    reaction_dict = {'rmg_reaction':rmg_reaction, 'family':family,'atst':None}
    for possible_name in possible_names:
        kinetics_path = os.path.join(atst_dir, f'{possible_name}.kinetics')
        if os.path.exists(kinetics_path):
            io = InputOutput(reaction=atst_reaction)
            local_context = io.read_kinetics_file(kinetics_path)
            reaction_dict['atst'] = local_context['reaction'].kinetics
            found_result = True
            break
    reactions_to_process[possible_name] = reaction_dict
    
    
    
            
            
            
assert False

for family, reaction_dict in autotst_reactions.items():
    for reaction_string, rmg_reaction in reaction_dict.items():
        reactions_to_process[reaction_string] = {
            'atst1_kin':None,
            'atst2_kin':None,
            'rmg_reaction':rmg_reaction
        }
         
        
        # Checking if AutoTST 1.0 results exist
        io = InputOutput(reaction=Reaction(reaction_string))
        r, p = reaction_string.split('_')
        possible_names = get_possible_names(r.split('+'), p.split('+'))
        for possible_name in possible_names:
            
            #if os.path.exists(os.path.join(atst1_dir, family, f'{possible_name}.kinetics' )):
            #    local_context = io.read_kinetics_file(path=os.path.join(atst1_dir, family, f'{possible_name}.kinetics'))
            #    reactions_to_process[reaction_string]['atst1_kin'] = local_context['reaction'].kinetics
            #    if len(rmg_reaction.reactants) == 1:
            #        reactions_to_process[reaction_string]['atst1_kin']._A.units = "1/s"
            #    elif len(rmg_reaction.reactants) == 2:
            #        reactions_to_process[reaction_string]['atst1_kin']._A.units = "cm^3/(mol*s)"
                    
                    
            if os.path.exists(os.path.join(atst2_dir, possible_name, f'{possible_name}.kinetics')):
                local_context = io.read_kinetics_file(path=os.path.join(atst2_dir, possible_name, f'{possible_name}.kinetics'))
                reactions_to_process[reaction_string]['atst2_kin'] = local_context['reaction'].kinetics
                if len(rmg_reaction.reactants) == 1:
                    reactions_to_process[reaction_string]['atst2_kin']._A.units = "1/s"
                elif len(rmg_reaction.reactants) == 2:
                    reactions_to_process[reaction_string]['atst2_kin']._A.units = "cm^3/(mol*s)"

reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "[CH2]"> + <Molecule "[H]"> <=> <Molecule "[CH]"> + <Molecule "[H][H]"> to intra_H_migration, trying different combination...
inputoutput.py:217 read_kinetics_file INFO Reading existing kinetics file ../_fake_results/[CH2]+[H]_[CH]+[H][H].kinetics
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse 

reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "[CH]=O"> + <Molecule "[H]"> <=> <Molecule "[C]=O"> + <Molecule "[H][H]"> to intra_H_migration, trying different combination...
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "C"> + <Molecule "[CH2]"> <=> <Molecu

inputoutput.py:217 read_kinetics_file INFO Reading existing kinetics file ../_fake_results/CO+[H]_[CH2]O+[H][H].kinetics
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CO"> + <Molecule "[H]"> <=> <Molecule "C[O]"> + <Molecule "[H][H]"> to intra_H_migration, trying different combination...
inputoutput.py:217 read_kinetics_file INFO Reading existing kinetics file ../_fake_results/CO+[H]_C[O]+[H][H].kinetics
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
react

reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:441 get_labeled_reaction INFO Matched reaction to intra_H_migration family
reaction.py:437 get_labeled_reaction WARNING This reaction has been already labeled...                                 it seems that resonance structures or reactants and products exist.
reaction.py:438 get_labeled_reaction WARNING Skipping this duplicate for now
inputoutput.py:217 read_kinetics_file INFO Reading existing kinetics file ../_fake_results/[CH2]C=C_C=[C]C.kinetics
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "[CH2]C=C"> <=> <Molecule "[CH]=CC"> to H_Abstraction, trying different combination...
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "[CH2]C=C"> <=> <Molecule "[CH]=CC"> to H_A

inputoutput.py:217 read_kinetics_file INFO Reading existing kinetics file ../_fake_results/C#CC+[H]_C#C[CH2]+[H][H].kinetics
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:441 get_labeled_reaction INFO Matched reaction to R_Addition_MultipleBond family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "C=[C]C"> <=> <Molecule "C#CC"> + <Molecule "[H]"> to intra_H_migration, trying different combination...
inputoutput.py:217 read_kinetics_file INFO Reading existing kinetics file ../_fake_results/C#CC+[H]_C=[C]C.kinetics
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:

...

reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CCCCCC(C)C"> + <Molecule "CCCCCC(C)(C)O[O]"> <=> <Molecule "[CH2]C(C)CCCCC"> + <Molecule "CCCCCC(C)(C)OO"> to intra_H_migration, trying different combination...
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CCCCCC(C)C"> + <Molecule "CC(C)CCCC(C)O[O]"> <=> <Molecule "[CH2]CCCCC(C)C"> + <Molecule "CC(C)CCCC(C)OO"> to intra_H_migration, trying different combination...
reaction.py:404 get_labeled_reaction INFO Trying to match re

reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CCCCCC(C)C"> + <Molecule "CC(C)CCCC(C)O[O]"> <=> <Molecule "CCCCC[C](C)C"> + <Molecule "CC(C)CCCC(C)OO"> to intra_H_migration, trying different combination...
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CCCC

reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CCCCCC(C)C"> + <Molecule "CCC(CCC(C)C)O[O]"> <=> <Molecule "CCCC[CH]C(C)C"> + <Molecule "CCC(CCC(C)C)OO"> to intra_H_migration, trying different combination...
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_re

reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CCCCCC(C)C"> + <Molecule "CCCCCC(C)(C)O[O]"> <=> <Molecule "CC[CH]CCC(C)C"> + <Molecule "CCCCCC(C)(C)OO"> to intra_H_migration, trying different combination...
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to H_Abstraction
reaction.py:441 get_labeled_reaction INFO Matched reaction to H_Abstraction family
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to R_Addition_MultipleBond
reaction.py:415 get_labeled_reaction ERROR Unable to determine a reaction for the forward direction. Trying the reverse direction.
reaction.py:404 get_labeled_reaction INFO Trying to match reaction to intra_H_migration
reaction.py:424 get_labeled_reaction ERROR Couldn't match <Molecule "CCCCCC(C)C"> + <Molecule "CC(C)CCCCCO[O]"> <=> <Molecule "CCC[CH]CC(C)C"> + <Molecule "CC(C)CCCCCOO"> to intra_H_migration, trying different combination...
reaction.py:404 get_labeled_reaction INFO Trying to match reaction

AssertionError: 

In [30]:
import pandas as pd
df = pd.DataFrame(reactions_to_process).T[['atst', 'rmg_reaction']]
df

atst  \
[CH2]+[H]_[CH]+[H][H]                               Arrhenius(A=(1.1778e+08,'cm^3/(mol*s)'), n=1.7...   
[CH2]+[H][H]_[CH3]+[H]                              Arrhenius(A=(26.0132,'cm^3/(mol*s)'), n=3.4950...   
C+[H]_[CH3]+[H][H]                                  Arrhenius(A=(119.435,'cm^3/(mol*s)'), n=3.4783...   
[H]+[OH]_[H][H]+[O]                                                                              None   
[H][H]+[OH]_O+[H]                                   Arrhenius(A=(2.06795e+07,'cm^3/(mol*s)'), n=2....   
...                                                                                               ...   
CCC[CH]CC(C)C+CCCCC(OO)C(C)C_CCCCC(O[O])C(C)C+C...                                               None   
CCC[CH]CC(C)C+CCCCCC(C)(C)OO_CCCCCC(C)(C)O[O]+C...                                               None   
CCC[CH]CC(C)C+CCCCCC(C)COO_CCCCCC(C)CO[O]+CCCCC...                                               None   
CC[CH]CCC(C)C+CCCCCC(C)COO_CCCCCC(C)CO[O]+CCCCC...                                               None   
CC[CH]CCC(C)C+CC(C)CCCC(C)OO_CC(C)CCCC(C)O[O]+C...                                               None   

                                                                                         rmg_reaction  
[CH2]+[H]_[CH]+[H][H]                                                          CH2(S) + H <=> CH + H2  
[CH2]+[H][H]_[CH3]+[H]                                                           CH2 + H2 <=> H + CH3  
C+[H]_[CH3]+[H][H]                                                               CH4 + H <=> CH3 + H2  
[H]+[OH]_[H][H]+[O]                                                                 O + H2 <=> H + OH  
[H][H]+[OH]_O+[H]                                                                 OH + H2 <=> H + H2O  
...                                                                                               ...  
CCC[CH]CC(C)C+CCCCC(OO)C(C)C_CCCCC(O[O])C(C)C+C...  c8h18-2 + c8h17oo-3-2 <=> c8h17-2d + c8h17ooh-3-2  
CCC[CH]CC(C)C+CCCCCC(C)(C)OO_CCCCCC(C)(C)O[O]+C...  c8h18-2 + c8h17oo-2-2 <=> c8h17-2d + c8h17ooh-2-2  
CCC[CH]CC(C)C+CCCCCC(C)COO_CCCCCC(C)CO[O]+CCCCC...  c8h18-2 + c8h17oo-1-2 <=> c8h17-2d + c8h17ooh-1-2  
CC[CH]CCC(C)C+CCCCCC(C)COO_CCCCCC(C)CO[O]+CCCCC...  c8h18-2 + c8h17oo-1-2 <=> c8h17-2e + c8h17ooh-1-2  
CC[CH]CCC(C)C+CC(C)CCCC(C)OO_CC(C)CCCC(C)O[O]+C...  c8h18-2 + c8h17oo-6-2 <=> c8h17-2e + c8h17ooh-6-2  

[2969 rows x 2 columns]

In [ ]:
cantera_strings = {}
for rxn_string, rmg_reaction, arrhenius2 in zip(df.index, df.rmg_reaction, df.atst2_kin):
    #print(rmg_reaction, arrhenius)
    cantera_strings[rxn_string] = {}
    
    #rmg_reaction.kinetics = arrhenius1
    #chemkin_string = rmg_reaction.to_chemkin(species_list)
    #chemkin_string = '\n'.join([l for l in chemkin_string.splitlines() if not l.startswith('!')])
    #print(chemkin_string)
    #cantera_reaction1, reverse_reaction = parser.readKineticsEntry(str(chemkin_string), False)
    #cantera_strings[rxn_string]['atst1_cti_rxn'] = cantera_reaction1
    
    
    rmg_reaction.kinetics = arrhenius2
    chemkin_string = rmg_reaction.to_chemkin(species_list)
    chemkin_string = '\n'.join([l for l in chemkin_string.splitlines() if not l.startswith('!')])
    print(chemkin_string)
    cantera_reaction2, reverse_reaction = parser.readKineticsEntry(str(chemkin_string), False)
    cantera_strings[rxn_string]['atst2_cti_rxn'] = cantera_reaction2
    
    cantera_strings[rxn_string]['cti_string'] = str(cantera_reaction2)
    print()

In [ ]:

for index, value in zip(pd.DataFrame(cantera_strings).index, pd.DataFrame(cantera_strings).values):
    df[index] = value
    
df.head()

In [ ]:
original_reactions = []
#modified_reactions_atst1 = []
modified_reactions_atst2 = []
modified_indicies = []
for i, parser_reaction in enumerate(parser.reactions):
    original_reactions.append(parser_reaction)
    assert original_reactions[i] == parser.reactions[i]
    #modified_reactions_atst1.append(parser_reaction)
    modified_reactions_atst2.append(parser_reaction)
    #print(str(parser_reaction))
    parser_string = ' '.join(str(parser_reaction).replace('(+ M)', '').split())
    if parser_string in list(df.cti_string):
        cti_df = df[df.cti_string == parser_string]
        assert cti_df.shape[0] == 1
        rxn_string = cti_df.index[0]
        #atst1_cti_rxn = cti_df.atst1_cti_rxn[0]
        atst2_cti_rxn = cti_df.atst2_cti_rxn[0]
        
        
        #atst1_cti_rxn.comment = "Reaction {:5d} has been replaced with AutoTST 1.0  #".format(i+1).upper()
        #parser.reactions[i] = atst1_cti_rxn
        #modified_reactions_atst1[i] = atst1_cti_rxn
        #header = ["#########################################################",
        #          "##  Reaction {:5d} has been replaced with AutoTST 1.0  ##".format(i+1),
        #          "##  Rxn String: {:38s} ##".format(rxn_string),
        #          "#########################################################"]
        #for h in header:
        #    print(h.strip())
        #parser.writeCTI(header=header, outName=os.path.join("..", "cantera-files", "autotst.1.{}.cti".format(i+1)))

        
        atst2_cti_rxn.comment = "Reaction {:5d} has been replaced with AutoTST 2.0  #".format(i+1).upper()
        parser.reactions[i] = atst2_cti_rxn
        modified_reactions_atst2[i] = atst2_cti_rxn
        header = ["#########################################################",
                  "##  Reaction {:5d} has been replaced with AutoTST 2.0  ##".format(i+1),
                  "##  Rxn String: {:38s} ##".format(rxn_string),
                  "#########################################################"]
        for h in header:
            print(h.strip())
        parser.writeCTI(header=header, outName=os.path.join("..", "cantera-files", "autotst.2.{}.cti".format(i+1)))

        parser.reactions[i] = original_reactions[i]
        
        modified_indicies.append([f'{i+1}', rxn_string])
        print()

        



In [ ]:
parser.reactions = modified_reactions_atst2

header = ["############################################################",
          "##    Many reactions have been modified by AutoTST 2.0    ##",
          "## Idx  : Reaction String                                 ##",
          "## ------------------------------------------------------ ##"
         ]

for i, rxn_string in modified_indicies:
    header.append("## {:4s} : {:48s}##".format(i, rxn_string))

header.append("###########################################################")

parser.writeCTI(header=header, outName=os.path.join("..", "cantera-files", "autotst.2.all.cti".format(i)))

In [ ]:
all_models = sorted(os.listdir('../cantera-files/'))
to_write = ["---\n"]
for model in all_models:
    model = model.split("/")[-1]

    to_write += [
        """{}:\n""".format(model),
        """    O2: "o2" \n""",
        """    N2: "n2" \n""",
        """    Ar: "ar" \n""",
        """    CO2: "co2" \n""",
        """    H2O: "h2o" \n""",
        """    n-butanol: "nc4h9oh" \n""",
        "\n"
    ]

with open('species-keys.yaml', "w") as f:
    f.writelines(to_write)


data_lists = sorted([f+"\n" for f in os.listdir('data/') if f.endswith(".yaml")])
with open('datalist.txt', "w") as f:
    f.writelines(data_lists)
